# 5) Functions

Last time:
- Introduction to Fortran

Today: 
 1. Using Julia  
 2. Introduction to floating point arithmetic   
     2.1. Plotting    
 3. Machine Epsilon

# 1. Julia

To recap from first class, Julia is a relatively new programming language. Think of it as MATLAB done right, open source, and fast. It's nominally general-purpose, but mostly for numerical/scientific/statistical computing. There are great [learning resources](https://julialang.org/learning/). We'll introduce concepts and language features as we go.

In [ ]:
# The last line of a cell is output by default
x = 3
y = 4

In [ ]:
println("$x + $y = $(x + y)") # string formatting/interpolation
4;  # trailing semicolon suppresses output

In [ ]:
@show x + y
x * y

## 1.1. Numbers

:::{tip}
Check this very helpful [Julia documentation page](https://docs.julialang.org/en/v1/manual/integers-and-floating-point-numbers/).
:::

In [ ]:
3, 3.0, 3.0f0, big(3.0) # integers, double precision, single precision, and convert to a maximum precision representation

In [ ]:
typeof(3), typeof(3.0), typeof(3.0f0), typeof(big(3.0))

In [ ]:
# automatic promotion
@show 3 + 3.0
@show 3.0 + 3.0f0
@show 3 + 3.0f0;

In [ ]:
# floating and integer division
@show 4 / 2
@show -3 ÷ 2; # type `\div` and press TAB

## 1.2 Arrays

In [ ]:
[1, 2, 3]

In [ ]:
# explicit typing
Float64[1,2,3]

In [ ]:
# promotion rules similar to arithmetic
[1,2,3.] + [1,2,3]

In [ ]:
x = [10., 20, 30]
x[2] # one-based indexing

In [ ]:
x[2] = 3.5

In [ ]:
# multi-dimensional array
A = [10 20 30; 40 50 60]

Compare with the Python notation:

```python
A = np.array([[10, 20, 30], [40, 50, 60]])
```

## 1.3 Functions

In [ ]:
# define a function called 'f' that takes three arguments, one of which has a default value
function f(x, y; z=3)
    sqrt(x*x + y*y) + z
end

# define another function also called 'f' that only takes two arguments
function f(x, y)
    sqrt(x*x + y*y)
end

What is the difference between a **method** and a **function** in Julia? Check this [resource](https://docs.julialang.org/en/v1/manual/methods/).

In [ ]:
# if I invoke f this way, which one will the Julia compiler use?
f(3, 4, z=5)

In [ ]:
# if instead I invoke f this way, which one will the Julia compiler use?
f(2, 3)

There are also compact "assignment form" function definitions:

In [ ]:
g(x, y) = sqrt(x^2 + y^2)
g(3, 4)

In the assignment form above, the body of the function must be a single expression, although it can be a compound expression.

We have just seen an example of one of the most powerful features of Julia: **dynamic [(multiple) dispatch](https://en.wikipedia.org/wiki/Multiple_dispatch)**: 

- Functions can have multiple definitions as long each definition restricts the type of the parameters differently. It is the type of the parameters that define which "definition" (or "method" in Julia terminology) will be called. 

- This is the way Julia mimics [polymorphism](https://en.wikipedia.org/wiki/Polymorphism_(computer_science)) that some compiled languages (e.g., C++) have.

**Anonymous functions** are usually functions so short-lived that they do not need a name. This is done with an arrow notation. Example:

In [ ]:
((x, y) -> sqrt(x^2 + y^2))(3, 4)

### Argument Passing Behavior

Julia function arguments follow a convention sometimes called "_pass-by-sharing_", which means that values are not copied when they are passed to functions. Function arguments themselves act as new variable _bindings_ (new "names" that can refer to values), much like assignments `argument_name = argument_value`, so that the objects they refer to are identical to the passed values. Modifications to mutable values (such as `Array`s) made within a function will be visible to the caller. (This is the same behavior found in Scheme, most Lisps, Python, Ruby and Perl, among other dynamic languages.)

As a common convention in Julia (_not_ a syntactic requirement), a function that modifies any of its arguments would typically be named with a `!`, e.g., `f!(x, y)` rather than `f(x, y)`, as a _visual reminder_ at the call site that at least one of the arguments (often the first one) is being mutated.

To read more about [ Julia functions](https://docs.julialang.org/en/v1/manual/functions/), check the Julia documentation.

### Argument-type declarations

You can declare the types of function arguments by appending `::TypeName` to the argument name. Example:


In [ ]:
function f(x::Float64, y::Float64)
    sqrt(x*x + y*y)
end



**Note**: Argument-type declarations normally have no impact on performance: regardless of what argument types (if any) are declared, Julia compiles a specialized version of the function for the **actual argument types passed by the caller**. 

The most common reasons to declare argument types in Julia are, instead: dispatch, correctness, and clarity.

## 1.4 Loops

In [ ]:
# ranges
1:50000000

In [ ]:
collect(1:5)

In [ ]:
x = 0
for n in 1:50000000
    x += 1/n^2
end
@show x
x - pi^2/6 # Basel problem (solved by Euler; generalized by Riemann's zeta function)

In [ ]:
# list comprehensions
sum([1/n^2 for n in 1:1000])

# 2. Floating point arithmetic

In [ ]:
0.1 + 0.2
(1 + 1.2e-16) - 1

In [ ]:
using Pkg
Pkg.add("Plots")

using Plots
default(linewidth=4)
plot(x -> (1 + x) - 1, xlims=(-1e-15, 1e-15),
xlabel="x", ylabel="y")
plot!(x -> x)

# 3. Machine epsilon

We approximate real numbers with **floating point** arithmetic, which can only represent discrete values. In particular, there exists a largest number, which we call $\epsilon_{\text{machine}}$, such that
$$ 1 \oplus x = 1 \quad \text{for all}\  \lvert x \rvert < \epsilon_{\text{machine}}.$$

The notation $\oplus, \ominus, \odot, \oslash$ represent the elementary operation carried out in floating point arithmetic.

In [ ]:
eps = 1
while 1 + eps != 1
    eps = eps / 2
end
eps

In [ ]:
eps = 1.f0
while 1 + eps != 1
    eps = eps / 2
end
eps

## 3.1 Approximating `exp`

$$e^x = 1 + x + \frac{x^2}{2!} + \frac{x^3}{3!} + \dotsb$$

Suppose we want to compute $f(x) = e^x - 1$ for small values of $x$.

In [ ]:
f1(x) = exp(x) - 1
y1 = f1(1e-8)

In [ ]:
f2(x) = x + x^2/2 + x^3/6
y2 = f2(1e-8)

Which answer is more accurate?

In [ ]:
@show (y1 - y2)        # Absolute difference
@show (y1 - y2) / y2;  # Relative difference

In [ ]:
0 / 0